In [12]:
from ctransformers import AutoModelForCausalLM, AutoConfig
import utils
import json
from llama_cpp import Llama

# load model .gguf bằng CTransformers


def configure():
    path = "models/theblokeai/Mistral-7B-Instruct-v0.2.Q4_K_M"
    # llm = CTransformers(
    #     model=path, max_new_tokens=1024, context_length=1024, gpu_layers=20
    # )
    # llm = AutoModelForCausalLM.from_pretrained(
    #     path=path,
    #     model_file="mistral-7b-instruct-v0.2.Q4_K_M.gguf",
    #     local_files_only=True,
    #     config = 
    # )
    llm = Llama(
        model_path=path+"/mistral-7b-instruct-v0.2.Q4_K_M.gguf",  # Download the model file first
        n_ctx=1024,  # The max sequence length to use - note that longer sequence lengths require much more resources
        n_threads=4,  # The number of CPU threads to use, tailor to your system and the resulting performance
        n_batch=1024,
        verbose=False, # Verbose = True to see full configuration, but expect output logs on every model call
        # n_gpu_layers=35,  # The number of layers to offload to GPU, if you have GPU acceleration available
    )
    db = utils.ArxivChroma()
    sqldb = utils.ArxivSQL()
    print("Configuration ok")
    return llm, sqldb, db


model, sqldb, db = configure()

Configuration ok


In [2]:
def extract_keyword_prompt(query):
    """A prompt that return a JSON block as arguments for querying database"""

    prompt = (
        """[INST] You are an assistant that choose only one action below based on guest question.
   1. If the guest question is asking for some specific document or article, you need to respond the information in JSON format with 2 keys "title", "author" if found any above. The authors are separated with the word 'and'. 
   2. If the guest question is asking for relevant informations about a topic, you need to respond the information in JSON format with 2 keys "keywords", "description", include a list of keywords represent the main academic topic, \
     and a description about the main topic. You may paraphrase the keywords to add more. \
   3. If the guest is not asking for any informations or documents, you need to respond with a polite answer in JSON format with 1 key "answer".
   QUESTION: '{query}'
   [/INST]
   ANSWER: 
   """
    ).format(query=query)

    return prompt

def make_answer_prompt(input, contexts):
    """A prompt that return the final answer, based on the queried context"""

    prompt = (
        """[INST] You are an library assistant that help to search articles and documents based on user's question.
  From guest's question, you have found some records and documents that may help. Now you need to answer the guest with the information found.
  You should answer in a conversational form politely.
  QUESTION: '{input}'
  INFORMATION: '{contexts}'
  [/INST]
  ANSWER:
  """
    ).format(input=input, contexts=contexts)

    return prompt

In [15]:
def response(args):
    """Create response context, based on input arguments"""
    keys = list(dict.keys(args))
    if "answer" in keys:
        return args['answer'], None  # trả lời trực tiếp
    if "keywords" in keys:
        # perform query
        query_texts = args["description"]
        keywords = args["keywords"]
        results = db.query_relevant(keywords=keywords, query_texts=query_texts)
        # print(results)
        ids = results['metadatas'][0]
        paper_id = [id['paper_id'] for id in ids]
        paper_info = sqldb.query_id(paper_id)
        # print(paper_info)
        records = [] # get title (2), author (3), link (6)
        result_string = ""
        for i in range(len(paper_id)):
            result_string += "Title: {}, Author: {}, Link: {}".format(paper_info[i][2],paper_info[i][3],paper_info[i][6])
            records.append([paper_info[i][2],paper_info[i][3],paper_info[i][6]])
        # process results:
        return result_string, records
        # invoke llm and return result
    if "title" in keys:
        results = sqldb.query(title = args['title'],author = args['author'])
        print(results)
        paper_info = sqldb.query(title = args['title'],author = args['author'])
        # if query not found then go crawl brh
        # -------------------------------------
        records = [] # get title (2), author (3), link (6)
        result_string = ""
        for i in range(len(paper_info)):
            result_string += "Title: {}, Author: {}, Link: {}".format(paper_info[i][2],paper_info[i][3],paper_info[i][6])
            records.append([paper_info[i][2],paper_info[i][3],paper_info[i][6]])
        # process results:
        if len(result_string) == 0:
            return "Information not found", None
        return result_string, records
        # invoke llm and return result

In [23]:
# test first step
# input_prompt = input()
input_prompt = "I'm working on a LSTM model to recognize actions in a video, recommend me some related papers"
first_prompt = extract_keyword_prompt(input_prompt)
# print(first_prompt)
# answer = model.invoke(first_prompt,
#                       temperature=0.0) # ctrans
answer = model(prompt=first_prompt,
               temperature=0.0) # llama
print("--------------------------")
print(answer)
args = json.loads(utils.trimming(answer))
# print(args)
response(args)

--------------------------
 {
      "keywords": ["LSTM model", "video analysis", "action recognition"],
      "description": "For recognizing actions in videos using Long Short-Term Memory (LSTM) models, you may find the following papers insightful. These studies explore various aspects of action recognition using LSTM: (1) 'Action Recognition with 3D Convolutional Neural Networks and Long Short-Term Memory' by Tran et al., 2015; (2) 'ConvLSTM: A Convolutional Neural Network for Video Recognition' by Shi et al., 2015; (3) 'Using Long-Short Term Memory for Action Recognition in Videos' by Graves, 2013."
    }
For recognizing actions in videos using Long Short-Term Memory (LSTM) models, you may find the following papers insightful. These studies explore various aspects of action recognition using LSTM: (1) 'Action Recognition with 3D Convolutional Neural Networks and Long Short-Term Memory' by Tran et al., 2015; (2) 'ConvLSTM: A Convolutional Neural Network for Video Recognition' by Shi 

In [10]:
# test response, second step
input_prompt = "I'm working on a LSTM model to recognize actions in a video, recommend me some related papers"
args =  {
      "keywords": ["LSTM model", "video analysis", "action recognition"],
      "description": "For recognizing actions in videos using Long Short-Term Memory (LSTM) models, you may find the following papers insightful. These studies explore various aspects of action recognition using LSTM: (1) 'Action Recognition with 3D Convolutional Neural Networks and Long Short-Term Memory' by Tran et al., 2015; (2) 'ConvLSTM: A Convolutional Neural Network for Video Recognition' by Shi et al., 2015; (3) 'Using Long-Short Term Memory for Action Recognition in Videos' by Graves, 2013."
    }
contexts, results = response(args)
if not results:
  # direct answer
    print(contexts)
else:
  output_prompt = make_answer_prompt(input_prompt,contexts)
  # answer = model.invoke(output_prompt,
  #                       temperature=0.3) # ctrans
  answer = model(prompt=output_prompt,
               temperature=0.0,
               max_tokens=1024,
               ) # llama
  print("------------------------")
  print(answer['choices'][0]['text'])

For recognizing actions in videos using Long Short-Term Memory (LSTM) models, you may find the following papers insightful. These studies explore various aspects of action recognition using LSTM: (1) 'Action Recognition with 3D Convolutional Neural Networks and Long Short-Term Memory' by Tran et al., 2015; (2) 'ConvLSTM: A Convolutional Neural Network for Video Recognition' by Shi et al., 2015; (3) 'Using Long-Short Term Memory for Action Recognition in Videos' by Graves, 2013.
['LSTM model', 'video analysis', 'action recognition']


Llama.generate: prefix-match hit

llama_print_timings:        load time =  139768.70 ms
llama_print_timings:      sample time =     140.16 ms /   412 runs   (    0.34 ms per token,  2939.41 tokens per second)
llama_print_timings: prompt eval time =       0.00 ms /     1 tokens (    0.00 ms per token,      inf tokens per second)
llama_print_timings:        eval time =   91570.34 ms /   412 runs   (  222.26 ms per token,     4.50 tokens per second)
llama_print_timings:       total time =   93048.98 ms /   413 tokens


------------------------
Hello there! I see that you're working on an LSTM model for recognizing actions in videos. I have found some related papers that might be of interest to you.

  1. The first one is titled "Action in Mind: A Neural Network Approach to Action Recognition and Segmentation" by Zahra Gharae. This paper proposes a neural network approach for action recognition and segmentation, which could provide some insights into your work with LSTM models. You can find it at this link: <http://arxiv.org/pdf/2104.14870v1>

  2. Another interesting paper is "Deep Neural Networks in Video Human Action Recognition: A Review" by Zihan Wang, Yang Yang, Zhi Liu, and Yifan Zhen. This review discusses the application of deep neural networks for video human action recognition. It could give you a broader perspective on the current state-of-the-art methods in this field. You can access it here: <http://arxiv.org/pdf/2305.15692v1>

  3. Lastly, there's "3D Convolutional Neural Networks for U

In [16]:
# full chain
# inference time depends on hardware ability :')
# with CPU i7-8750H, 16GB RAM and no GPU cuda, expect inference time up to 5-6 min
# input_prompt = input()
input_prompt = "I'm working on a LSTM model to recognize actions in a video, recommend me some related papers"
first_prompt = extract_keyword_prompt(input_prompt)
# print(first_prompt)
# answer = model.invoke(first_prompt,
#                       temperature=0.0) # ctrans, answer is a string
answer = model(prompt=first_prompt,
               temperature=0.0,
               max_tokens=512,
               ) # llama, answer is a dict
print("--------------------------")
# print(answer['choices'][0]['text']) # see middle answer
args = json.loads(utils.trimming(answer['choices'][0]['text']))
contexts, results = response(args)
if not results:
  # direct answer
    print(contexts)
else:
  output_prompt = make_answer_prompt(input_prompt,contexts)
  # answer = model.invoke(output_prompt,
  #                       temperature=0.3) # ctrans, answer is a string
  answer = model(prompt=output_prompt,
               temperature=0.0,
               max_tokens=1024,
               ) # llama, answer is a dict
  print("--------------------------")
  print(answer['choices'][0]['text'])

--------------------------
------------------------
Hello there! I see that you're working on an LSTM model for recognizing actions in videos. I have some related papers that might be of interest to you.

  1. The first paper is titled "Deep Neural Networks in Video Human Action Recognition: A Review" by Zihan Wang, Yang Yang, Zhi Liu, and Yifan Zhen. This review discusses the application of deep neural networks in recognizing human actions from videos. You can find it at this link: <http://arxiv.org/pdf/2305.15692v1>

  2. The second paper is titled "A Video Recognition Method by using Adaptive Structural Learning of Long Short Term Memory based Deep Belief Network" by Shin Kamada and Takumi Ichimur. This study proposes a method for video recognition using an adaptive structural learning LSTM-DBN model. You can access it at this link: <http://arxiv.org/pdf/1909.13480v1>

  3. Lastly, there's the paper "3D Convolutional Neural Networks for Ultrasound-Based Silent Speech Interfaces" by 

In [17]:
!pip freeze > requirements.txt